In [27]:
import numpy as np
import pandas as pd
import json
import matplotlib.pyplot as plt
from statsmodels.tsa.arima.model import ARIMA
import matplotlib.dates as mdates
from pandas.io.json import json_normalize

In [22]:
pd.options.display.max_columns = None;

In [2]:
df_raw = pd.read_json('test_2022_IKEA.json')

In [25]:
df_raw.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 68 entries, 0 to 67
Data columns (total 29 columns):
 #   Column              Non-Null Count  Dtype  
---  ------              --------------  -----  
 0   id                  68 non-null     int64  
 1   pointName           45 non-null     object 
 2   meterName           68 non-null     object 
 3   type                68 non-null     int64  
 4   positionId          54 non-null     float64
 5   positionIds         0 non-null      float64
 6   currentReading      54 non-null     float64
 7   distinguish         68 non-null     int64  
 8   manageTypeId        54 non-null     float64
 9   isDelete            0 non-null      float64
 10  typeName            52 non-null     object 
 11  createTime          68 non-null     object 
 12  deviceIds           0 non-null      float64
 13  relationPositionId  25 non-null     float64
 14  relationType        68 non-null     int64  
 15  property            68 non-null     int64  
 16  deviceTag 

In [26]:
df_raw.head(5)

id  pointName meterName  type  positionId  positionIds  currentReading  \
0   1  T100-Enrg      T100     1         2.0          NaN             0.0   
1   2  T112-Enrg      T112     1         3.0          NaN             0.0   
2   3  T184-Enrg      T184     1         3.0          NaN             0.0   
3   4       None      T160     1         4.0          NaN             0.0   
4   5  T172-Enrg      T172     1         5.0          NaN             0.0   

   distinguish  manageTypeId  isDelete typeName                    createTime  \
0            2           1.0       NaN     光伏用电  2021-12-22T07:45:30.000+0000   
1            2           1.0       NaN     光伏用电  2021-12-22T07:46:28.000+0000   
2            2           1.0       NaN     光伏用电  2021-12-22T07:47:11.000+0000   
3            2           1.0       NaN     光伏用电  2021-12-22T07:48:09.000+0000   
4            2           1.0       NaN     光伏用电  2021-12-22T07:49:01.000+0000   

   deviceIds  relationPositionId  relationType  property deviceTag  source  \
0        NaN                 NaN             3         1      T100     NaN   
1        NaN                 NaN             1         1      T112     NaN   
2        NaN                 NaN             1         1      T184     NaN   
3        NaN                 4.0             2         1      None     NaN   
4        NaN                 NaN             1         1      T172     NaN   

   parentId  childrenCount  accountId  isSyncData  meterAccountName  \
0         0            NaN        NaN         NaN               NaN   
1         0            NaN        NaN         NaN               NaN   
2         0            NaN        NaN         NaN               NaN   
3         0            NaN        NaN         NaN               NaN   
4         0            NaN        NaN         NaN               NaN   

   meterAccountId pointTag  pointSource                 syncStartTime  \
0             NaN     Enrg          NaN  2022-09-11T16:00:00.000+0000   
1             NaN     Enrg          NaN  2022-09-11T16:00:00.000+0000   
2             NaN     Enrg          NaN  2022-09-11T16:00:00.000+0000   
3             NaN     None          NaN                          None   
4             NaN     Enrg          NaN  2022-09-11T16:00:00.000+0000   

                    syncEndTime  \
0  2022-09-12T16:00:00.000+0000   
1  2022-09-12T16:00:00.000+0000   
2  2022-09-12T16:00:00.000+0000   
3                          None   
4  2022-09-12T16:00:00.000+0000   

                                         iotDataList  
0  [{'id': 'azwuxi|T100|Enrg', 'device': 'T100', ...  
1  [{'id': 'azwuxi|T112|Enrg', 'device': 'T112', ...  
2  [{'id': 'azwuxi|T184|Enrg', 'device': 'T184', ...  
3                                               None  
4  [{'id': 'azwuxi|T172|Enrg', 'device': 'T172', ...

* as observed here, this file is a nested json, and need to deal with this feature

In [34]:
with open('test_2022_IKEA.json') as data_file:    
    data = json.load(data_file)  


In [43]:
var_name = ['id',
"meterName",
'type',
'positionId']

In [48]:
df = pd.json_normalize(data, 'iotDataList',var_name,
record_prefix='iotDataList_')
                    

df1 = pd.json_normalize(data, 'iotDataList')

In [49]:
print('df:',len(df))
print('df1:',len(df1))

df: 85888
df1: 85888


In [51]:
df.head(3)

iotDataList_id iotDataList_device iotDataList_tag iotDataList_value  \
0  azwuxi|T100|Enrg               T100            Enrg       11692916.00   
1  azwuxi|T100|Enrg               T100            Enrg       11692916.00   
2  azwuxi|T100|Enrg               T100            Enrg       11692916.00   

           iotDataList_dataTime        iotDataList_createTime  \
0  2022-03-08T14:44:20.000+0000  2022-08-16T05:17:21.000+0000   
1  2022-03-08T14:54:27.000+0000  2022-08-16T05:17:21.000+0000   
2  2022-03-08T15:04:34.000+0000  2022-08-16T05:17:21.000+0000   

   iotDataList_year  iotDataList_month  iotDataList_day id meterName type  \
0                 0                  0                0  1      T100    1   
1                 0                  0                0  1      T100    1   
2                 0                  0                0  1      T100    1   

  positionId  
0          2  
1          2  
2          2

In [52]:
df1.head(3)

id device   tag        value                      dataTime  \
0  azwuxi|T100|Enrg   T100  Enrg  11692916.00  2022-03-08T14:44:20.000+0000   
1  azwuxi|T100|Enrg   T100  Enrg  11692916.00  2022-03-08T14:54:27.000+0000   
2  azwuxi|T100|Enrg   T100  Enrg  11692916.00  2022-03-08T15:04:34.000+0000   

                     createTime  year  month  day  
0  2022-08-16T05:17:21.000+0000     0      0    0  
1  2022-08-16T05:17:21.000+0000     0      0    0  
2  2022-08-16T05:17:21.000+0000     0      0    0

In [63]:
df.info()

<class 'pandas.core.frame.DataFrame'>
DatetimeIndex: 85888 entries, 2022-03-08 14:44:20+00:00 to 2022-08-16 16:00:00+00:00
Data columns (total 12 columns):
 #   Column                  Non-Null Count  Dtype  
---  ------                  --------------  -----  
 0   iotDataList_id          85888 non-null  object 
 1   iotDataList_device      85888 non-null  object 
 2   iotDataList_tag         85888 non-null  object 
 3   iotDataList_value       85888 non-null  float64
 4   iotDataList_createTime  85888 non-null  object 
 5   iotDataList_year        85888 non-null  int64  
 6   iotDataList_month       85888 non-null  int64  
 7   iotDataList_day         85888 non-null  int64  
 8   id                      85888 non-null  float64
 9   meterName               85888 non-null  object 
 10  type                    85888 non-null  float64
 11  positionId              85888 non-null  float64
dtypes: float64(4), int64(3), object(5)
memory usage: 8.5+ MB


In [54]:
df1.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 85888 entries, 0 to 85887
Data columns (total 9 columns):
 #   Column      Non-Null Count  Dtype 
---  ------      --------------  ----- 
 0   id          85888 non-null  object
 1   device      85888 non-null  object
 2   tag         85888 non-null  object
 3   value       85888 non-null  object
 4   dataTime    85888 non-null  object
 5   createTime  85888 non-null  object
 6   year        85888 non-null  int64 
 7   month       85888 non-null  int64 
 8   day         85888 non-null  int64 
dtypes: int64(3), object(6)
memory usage: 5.9+ MB


In [55]:
df['iotDataList_dataTime'] = pd.to_datetime(df['iotDataList_dataTime'])

In [67]:
df['iotDataList_createTime'] = pd.to_datetime(df['iotDataList_createTime'])

In [59]:
df.tail(5)

iotDataList_id iotDataList_device  \
iotDataList_dataTime                                                      
2022-08-15 22:31:33+00:00  azwuxi|waterZ02|WtrVolTot           waterZ02   
2022-08-16 03:31:33+00:00  azwuxi|waterZ02|WtrVolTot           waterZ02   
2022-08-16 04:12:00+00:00  azwuxi|waterZ02|WtrVolTot           waterZ02   
2022-08-16 10:31:33+00:00  azwuxi|waterZ02|WtrVolTot           waterZ02   
2022-08-16 16:00:00+00:00  azwuxi|waterZ02|WtrVolTot           waterZ02   

                          iotDataList_tag iotDataList_value  \
iotDataList_dataTime                                          
2022-08-15 22:31:33+00:00       WtrVolTot           6520.08   
2022-08-16 03:31:33+00:00       WtrVolTot           6812.18   
2022-08-16 04:12:00+00:00       WtrVolTot           6868.99   
2022-08-16 10:31:33+00:00       WtrVolTot           6992.28   
2022-08-16 16:00:00+00:00       WtrVolTot           6999.88   

                                 iotDataList_createTime  iotDataList_year  \
iotDataList_dataTime                                                        
2022-08-15 22:31:33+00:00  2022-08-16T02:17:09.000+0000                 0   
2022-08-16 03:31:33+00:00  2022-08-16T02:17:09.000+0000                 0   
2022-08-16 04:12:00+00:00  2022-08-16T02:17:09.000+0000                 0   
2022-08-16 10:31:33+00:00  2022-08-16T02:17:09.000+0000                 0   
2022-08-16 16:00:00+00:00  2022-08-16T02:17:09.000+0000                 0   

                           iotDataList_month  iotDataList_day   id  \
iotDataList_dataTime                                                 
2022-08-15 22:31:33+00:00                  0                0  126   
2022-08-16 03:31:33+00:00                  0                0  126   
2022-08-16 04:12:00+00:00                  0                0  126   
2022-08-16 10:31:33+00:00                  0                0  126   
2022-08-16 16:00:00+00:00                  0                0  126   

                            meterName type positionId  
iotDataList_dataTime                                   
2022-08-15 22:31:33+00:00  智能水总表02_勿动    2          2  
2022-08-16 03:31:33+00:00  智能水总表02_勿动    2          2  
2022-08-16 04:12:00+00:00  智能水总表02_勿动    2          2  
2022-08-16 10:31:33+00:00  智能水总表02_勿动    2          2  
2022-08-16 16:00:00+00:00  智能水总表02_勿动    2          2

In [58]:
df = df.set_index('iotDataList_dataTime')

In [61]:
# convert to numeric type
num_var = ['iotDataList_value','id', 'type', 'positionId']

In [62]:
# convert loop

for i in num_var:
    df[i] = df[i].astype(float)

In [64]:
df.describe()


iotDataList_value  iotDataList_year  iotDataList_month  \
count       8.588800e+04           85888.0            85888.0   
mean        1.118359e+07               0.0                0.0   
std         1.003586e+07               0.0                0.0   
min         1.200000e+01               0.0                0.0   
25%         2.279900e+06               0.0                0.0   
50%         6.950594e+06               0.0                0.0   
75%         1.859775e+07               0.0                0.0   
max         2.938098e+07               0.0                0.0   

       iotDataList_day            id          type    positionId  
count          85888.0  85888.000000  85888.000000  85888.000000  
mean               0.0      6.356196      1.004075      5.325238  
std                0.0      4.695829      0.064973      2.147101  
min                0.0      1.000000      1.000000      1.000000  
25%                0.0      3.000000      1.000000      3.000000  
50%                0.0      7.000000      1.000000      6.000000  
75%                0.0      9.000000      1.000000      7.000000  
max                0.0    126.000000      3.000000     23.000000

### the problem with the data
* though the start date is set to Jan2022, but the actual start date is in March 2022
* there's water data inside this table
* perhaps some missing date/time in the table, need to detect
* the added vars (year, month, day) has no meaning
* only 9 meters 

In [65]:
df = df.drop(columns=['iotDataList_year', 'iotDataList_month','iotDataList_day'])

In [71]:
df.info()

<class 'pandas.core.frame.DataFrame'>
DatetimeIndex: 85888 entries, 2022-03-08 14:44:20+00:00 to 2022-08-16 16:00:00+00:00
Data columns (total 9 columns):
 #   Column                  Non-Null Count  Dtype              
---  ------                  --------------  -----              
 0   iotDataList_id          85888 non-null  object             
 1   iotDataList_device      85888 non-null  object             
 2   iotDataList_tag         85888 non-null  object             
 3   iotDataList_value       85888 non-null  float64            
 4   iotDataList_createTime  85888 non-null  datetime64[ns, UTC]
 5   id                      85888 non-null  float64            
 6   meterName               85888 non-null  object             
 7   type                    85888 non-null  float64            
 8   positionId              85888 non-null  float64            
dtypes: datetime64[ns, UTC](1), float64(4), object(4)
memory usage: 6.6+ MB


In [77]:
list(df.dtypes[df.dtypes == object].index)


['iotDataList_id', 'iotDataList_device', 'iotDataList_tag', 'meterName']

In [79]:
# value counts
for i in list(df.dtypes[df.dtypes == object].index):
    print("*****"*5)
    print(df[i].value_counts())
    print("*****"*5)

*************************
azwuxi|T100|Enrg             9517
azwuxi|T2148|Enrg            9505
azwuxi|T2088|Enrg            9505
azwuxi|T2100|Enrg            9505
azwuxi|T2076|Enrg            9504
azwuxi|T184|Enrg             9503
azwuxi|T112|Enrg             9502
azwuxi|T172|Enrg             9502
azwuxi|T148|Enrg             9502
azwuxi|waterZ01|WtrVolTot      34
azwuxi|19160040|WtrVolTot      28
azwuxi|19174400|WtrVolTot      27
azwuxi|waterZ02|WtrVolTot      26
azwuxi|19160046|WtrVolTot      19
azwuxi|12262879|WtrVolTot      19
azwuxi|19160033|WtrVolTot      18
azwuxi|19160044|WtrVolTot      18
azwuxi|19160043|WtrVolTot      16
azwuxi|19160035|WtrVolTot      16
azwuxi|19160048|WtrVolTot      16
azwuxi|19160050|WtrVolTot      16
azwuxi|12150079|WtrVolTot      16
azwuxi|19160045|WtrVolTot      15
azwuxi|12742311|WtrVolTot      11
azwuxi|19160042|WtrVolTot      10
azwuxi|19160051|WtrVolTot       9
azwuxi|19160034|WtrVolTot       8
azwuxi|19174399|WtrVolTot       7
azwuxi|gasZ01|GasVolTo

#### As investigated, there's only 9 electricity meters available. below prediction is only based on these 9 meters

In [80]:
meterName = [

'T100',  
'T2148',        
'T2088' ,        
'T2100'  ,       
'T2076'   ,       
'T184',          
'T112',          
'T172',           
'T148'              
]

In [83]:
df_e = df.loc[df['meterName'].isin(meterName)]

In [84]:
df_e.info()

<class 'pandas.core.frame.DataFrame'>
DatetimeIndex: 85545 entries, 2022-03-08 14:44:20+00:00 to 2022-09-05 19:19:55+00:00
Data columns (total 9 columns):
 #   Column                  Non-Null Count  Dtype              
---  ------                  --------------  -----              
 0   iotDataList_id          85545 non-null  object             
 1   iotDataList_device      85545 non-null  object             
 2   iotDataList_tag         85545 non-null  object             
 3   iotDataList_value       85545 non-null  float64            
 4   iotDataList_createTime  85545 non-null  datetime64[ns, UTC]
 5   id                      85545 non-null  float64            
 6   meterName               85545 non-null  object             
 7   type                    85545 non-null  float64            
 8   positionId              85545 non-null  float64            
dtypes: datetime64[ns, UTC](1), float64(4), object(4)
memory usage: 6.5+ MB


In [85]:
df_e['meterName'].value_counts()


T100     9517
T2148    9505
T2088    9505
T2100    9505
T2076    9504
T184     9503
T112     9502
T172     9502
T148     9502
Name: meterName, dtype: int64

In [87]:
df_e['iotDataList_id'].value_counts()

azwuxi|T100|Enrg     9517
azwuxi|T2148|Enrg    9505
azwuxi|T2088|Enrg    9505
azwuxi|T2100|Enrg    9505
azwuxi|T2076|Enrg    9504
azwuxi|T184|Enrg     9503
azwuxi|T112|Enrg     9502
azwuxi|T172|Enrg     9502
azwuxi|T148|Enrg     9502
Name: iotDataList_id, dtype: int64

In [88]:
# create dataframe-dictionary

DictDF = {}

for i in meterName:
    DictDF[i] = df_e.loc[df_e['meterName'] == i]

In [89]:
meterName

['T100', 'T2148', 'T2088', 'T2100', 'T2076', 'T184', 'T112', 'T172', 'T148']

In [90]:
DictDF['T2076']


iotDataList_id iotDataList_device  \
iotDataList_dataTime                                              
2022-03-08 14:44:20+00:00  azwuxi|T2076|Enrg              T2076   
2022-03-08 14:54:27+00:00  azwuxi|T2076|Enrg              T2076   
2022-03-08 15:04:34+00:00  azwuxi|T2076|Enrg              T2076   
2022-03-08 15:14:41+00:00  azwuxi|T2076|Enrg              T2076   
2022-03-08 15:24:48+00:00  azwuxi|T2076|Enrg              T2076   
2022-03-08 15:34:55+00:00  azwuxi|T2076|Enrg              T2076   
2022-03-08 15:45:02+00:00  azwuxi|T2076|Enrg              T2076   
2022-03-08 15:55:09+00:00  azwuxi|T2076|Enrg              T2076   
2022-03-08 16:05:16+00:00  azwuxi|T2076|Enrg              T2076   
2022-03-08 16:15:23+00:00  azwuxi|T2076|Enrg              T2076   
2022-03-08 16:25:30+00:00  azwuxi|T2076|Enrg              T2076   
2022-03-08 16:35:37+00:00  azwuxi|T2076|Enrg              T2076   
2022-03-08 16:45:44+00:00  azwuxi|T2076|Enrg              T2076   
2022-03-08 16:55:51+00:00  azwuxi|T2076|Enrg              T2076   
2022-03-08 17:05:58+00:00  azwuxi|T2076|Enrg              T2076   
2022-03-08 17:16:05+00:00  azwuxi|T2076|Enrg              T2076   
2022-03-08 17:26:12+00:00  azwuxi|T2076|Enrg              T2076   
2022-03-08 17:36:19+00:00  azwuxi|T2076|Enrg              T2076   
2022-03-08 17:46:26+00:00  azwuxi|T2076|Enrg              T2076   
2022-03-08 17:56:33+00:00  azwuxi|T2076|Enrg              T2076   
2022-03-08 18:06:40+00:00  azwuxi|T2076|Enrg              T2076   
2022-03-08 18:16:47+00:00  azwuxi|T2076|Enrg              T2076   
2022-03-08 18:26:54+00:00  azwuxi|T2076|Enrg              T2076   
2022-03-08 18:37:01+00:00  azwuxi|T2076|Enrg              T2076   
2022-03-08 18:47:08+00:00  azwuxi|T2076|Enrg              T2076   
2022-03-08 18:57:15+00:00  azwuxi|T2076|Enrg              T2076   
2022-03-08 19:07:22+00:00  azwuxi|T2076|Enrg              T2076   
2022-03-08 19:17:29+00:00  azwuxi|T2076|Enrg              T2076   
2022-03-08 19:27:36+00:00  azwuxi|T2076|Enrg              T2076   
2022-03-08 19:37:43+00:00  azwuxi|T2076|Enrg              T2076   
2022-03-08 19:47:50+00:00  azwuxi|T2076|Enrg              T2076   
2022-03-08 19:57:57+00:00  azwuxi|T2076|Enrg              T2076   
2022-03-08 20:08:04+00:00  azwuxi|T2076|Enrg              T2076   
2022-03-08 20:18:11+00:00  azwuxi|T2076|Enrg              T2076   
2022-03-08 20:28:18+00:00  azwuxi|T2076|Enrg              T2076   
2022-03-08 20:38:25+00:00  azwuxi|T2076|Enrg              T2076   
2022-03-08 20:48:32+00:00  azwuxi|T2076|Enrg              T2076   
2022-03-08 20:58:39+00:00  azwuxi|T2076|Enrg              T2076   
2022-03-08 21:08:46+00:00  azwuxi|T2076|Enrg              T2076   
2022-03-08 21:18:53+00:00  azwuxi|T2076|Enrg              T2076   
2022-03-08 21:29:00+00:00  azwuxi|T2076|Enrg              T2076   
2022-03-08 21:39:07+00:00  azwuxi|T2076|Enrg              T2076   
2022-03-08 21:49:14+00:00  azwuxi|T2076|Enrg              T2076   
2022-03-08 21:59:21+00:00  azwuxi|T2076|Enrg              T2076   
2022-03-08 22:09:28+00:00  azwuxi|T2076|Enrg              T2076   
2022-03-08 22:19:35+00:00  azwuxi|T2076|Enrg              T2076   
2022-03-08 22:29:42+00:00  azwuxi|T2076|Enrg              T2076   
2022-03-08 22:39:49+00:00  azwuxi|T2076|Enrg              T2076   
2022-03-08 22:49:56+00:00  azwuxi|T2076|Enrg              T2076   
2022-03-08 23:00:03+00:00  azwuxi|T2076|Enrg              T2076   
2022-03-08 23:10:10+00:00  azwuxi|T2076|Enrg              T2076   
2022-03-08 23:20:17+00:00  azwuxi|T2076|Enrg              T2076   
2022-03-08 23:30:24+00:00  azwuxi|T2076|Enrg              T2076   
2022-03-08 23:40:31+00:00  azwuxi|T2076|Enrg              T2076   
2022-03-08 23:50:38+00:00  azwuxi|T2076|Enrg              T2076   
2022-03-09 00:00:45+00:00  azwuxi|T2076|Enrg              T2076   
2022-03-09 00:10:52+00:00  azwuxi|T2076|Enrg              T2076   
2022-03-09 00:20:59+00:00  azwuxi|T2076|Enrg              T2076   
2022-03-09

In [92]:
# calculate absolute value for consumption
for i in meterName:
    DictDF[i]['consump'] = DictDF[i]['iotDataList_value'].diff()


/var/folders/xj/93j1__ws08j4839__kqrvwtc0000gp/T/ipykernel_65996/851953927.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  DictDF[i]['consump'] = DictDF[i]['iotDataList_value'].diff()
/var/folders/xj/93j1__ws08j4839__kqrvwtc0000gp/T/ipykernel_65996/851953927.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  DictDF[i]['consump'] = DictDF[i]['iotDataList_value'].diff()
/var/folders/xj/93j1__ws08j4839__kqrvwtc0000gp/T/ipykernel_65996/851953927.py:3: SettingWithCopyWarning: 
A value is trying to be set on

In [95]:
DictDF['T172'].tail(100)



iotDataList_id iotDataList_device  \
iotDataList_dataTime                                             
2022-09-03 15:09:35+00:00  azwuxi|T172|Enrg               T172   
2022-09-03 15:19:37+00:00  azwuxi|T172|Enrg               T172   
2022-09-03 15:29:39+00:00  azwuxi|T172|Enrg               T172   
2022-09-03 15:39:41+00:00  azwuxi|T172|Enrg               T172   
2022-09-03 15:49:43+00:00  azwuxi|T172|Enrg               T172   
2022-09-03 15:59:45+00:00  azwuxi|T172|Enrg               T172   
2022-09-03 16:09:47+00:00  azwuxi|T172|Enrg               T172   
2022-09-03 16:19:49+00:00  azwuxi|T172|Enrg               T172   
2022-09-03 16:29:51+00:00  azwuxi|T172|Enrg               T172   
2022-09-03 16:39:53+00:00  azwuxi|T172|Enrg               T172   
2022-09-03 16:49:55+00:00  azwuxi|T172|Enrg               T172   
2022-09-03 16:59:57+00:00  azwuxi|T172|Enrg               T172   
2022-09-03 17:09:59+00:00  azwuxi|T172|Enrg               T172   
2022-09-03 17:20:01+00:00  azwuxi|T172|Enrg               T172   
2022-09-03 17:30:03+00:00  azwuxi|T172|Enrg               T172   
2022-09-03 17:40:05+00:00  azwuxi|T172|Enrg               T172   
2022-09-03 17:50:07+00:00  azwuxi|T172|Enrg               T172   
2022-09-03 18:00:09+00:00  azwuxi|T172|Enrg               T172   
2022-09-03 18:10:11+00:00  azwuxi|T172|Enrg               T172   
2022-09-03 18:20:13+00:00  azwuxi|T172|Enrg               T172   
2022-09-03 18:30:15+00:00  azwuxi|T172|Enrg               T172   
2022-09-03 18:40:17+00:00  azwuxi|T172|Enrg               T172   
2022-09-03 18:50:19+00:00  azwuxi|T172|Enrg               T172   
2022-09-03 19:00:21+00:00  azwuxi|T172|Enrg               T172   
2022-09-03 19:10:23+00:00  azwuxi|T172|Enrg               T172   
2022-09-03 19:20:25+00:00  azwuxi|T172|Enrg               T172   
2022-09-03 19:30:27+00:00  azwuxi|T172|Enrg               T172   
2022-09-03 19:40:29+00:00  azwuxi|T172|Enrg               T172   
2022-09-03 19:50:31+00:00  azwuxi|T172|Enrg               T172   
2022-09-03 20:00:33+00:00  azwuxi|T172|Enrg               T172   
2022-09-03 20:10:35+00:00  azwuxi|T172|Enrg               T172   
2022-09-03 20:20:37+00:00  azwuxi|T172|Enrg               T172   
2022-09-03 20:30:39+00:00  azwuxi|T172|Enrg               T172   
2022-09-03 20:40:40+00:00  azwuxi|T172|Enrg               T172   
2022-09-03 20:50:42+00:00  azwuxi|T172|Enrg               T172   
2022-09-03 21:00:44+00:00  azwuxi|T172|Enrg               T172   
2022-09-03 21:10:46+00:00  azwuxi|T172|Enrg               T172   
2022-09-05 09:07:54+00:00  azwuxi|T172|Enrg               T172   
2022-09-05 09:17:56+00:00  azwuxi|T172|Enrg               T172   
2022-09-05 09:27:58+00:00  azwuxi|T172|Enrg               T172   
2022-09-05 09:38:00+00:00  azwuxi|T172|Enrg               T172   
2022-09-05 09:48:02+00:00  azwuxi|T172|Enrg               T172   
2022-09-05 09:58:04+00:00  azwuxi|T172|Enrg               T172   
2022-09-05 10:08:06+00:00  azwuxi|T172|Enrg               T172   
2022-09-05 10:18:08+00:00  azwuxi|T172|Enrg               T172   
2022-09-05 10:28:10+00:00  azwuxi|T172|Enrg               T172   
2022-09-05 10:38:12+00:00  azwuxi|T172|Enrg               T172   
2022-09-05 10:48:14+00:00  azwuxi|T172|Enrg               T172   
2022-09-05 10:58:16+00:00  azwuxi|T172|Enrg               T172   
2022-09-05 11:08:18+00:00  azwuxi|T172|Enrg               T172   
2022-09-05 11:18:20+00:00  azwuxi|T172|Enrg               T172   
2022-09-05 11:28:22+00:00  azwuxi|T172|Enrg               T172   
2022-09-05 11:38:24+00:00  azwuxi|T172|Enrg               T172   
2022-09-05 11:48:26+00:00  azwuxi|T172|Enrg               T172   
2022-09-05 11:58:28+00:00  azwuxi|T172|Enrg               T172   
2022-09-05 12:08:30+00:00  azwuxi|T172|Enrg               T172   
2022-09-05 12:18:32+00:00  azwuxi|T172|Enrg               T172   
2022-09-05 12:28:33+00:00  azwuxi|T172|Enrg               T172   
2022-09-05 12:38:35+00:00  azwuxi|T172|Enrg               T172   
202

In [97]:
for i in meterName:
   print('-'*5, i, "-"*5)
   print(DictDF[i]['consump'].describe())
   print("*"*100)

----- T100 -----
count    9.516000e+03
mean     1.596914e+02
std      4.610923e+05
min     -1.310874e+07
25%      0.000000e+00
50%      3.800000e+01
75%      7.100000e+01
max      1.297439e+07
Name: consump, dtype: float64
****************************************************************************************************
----- T2148 -----
count     9504.000000
mean        31.001368
std        877.698501
min     -24268.000000
25%          9.000000
50%         12.000000
75%         14.000000
max      55500.000000
Name: consump, dtype: float64
****************************************************************************************************
----- T2088 -----
count     9504.000000
mean        36.938342
std       1016.300009
min     -26499.000000
25%         12.000000
50%         15.000000
75%         16.000000
max      57751.000000
Name: consump, dtype: float64
****************************************************************************************************
----- T2100 -----
count   

In [98]:
# combine consumption in a single dataframe

combine_df = pd.DataFrame()

In [99]:
for i in meterName:
    combine_df[i] = DictDF[i]['consump'].resample('D').sum()

In [100]:
combine_df


T100    T2148    T2088  T2100  T2076      T184  \
iotDataList_dataTime                                                            
2022-03-08 00:00:00+00:00       0.0    466.0    528.0    0.0    0.0       0.0   
2022-03-09 00:00:00+00:00       0.0   1352.0   1483.0    0.0    0.0       0.0   
2022-03-10 00:00:00+00:00       0.0   1424.0   1518.0    0.0    0.0       0.0   
2022-03-11 00:00:00+00:00       0.0   1062.0   1191.0    0.0    0.0       0.0   
2022-03-12 00:00:00+00:00       0.0      0.0      0.0    0.0    0.0       0.0   
2022-03-13 00:00:00+00:00       0.0      0.0      0.0    0.0    0.0       0.0   
2022-03-14 00:00:00+00:00       0.0      0.0      0.0    0.0    0.0       0.0   
2022-03-15 00:00:00+00:00       0.0      0.0      0.0    0.0    0.0       0.0   
2022-03-16 00:00:00+00:00       0.0      0.0      0.0    0.0    0.0       0.0   
2022-03-17 00:00:00+00:00       0.0      0.0      0.0    0.0    0.0       0.0   
2022-03-18 00:00:00+00:00       0.0      0.0      0.0    0.0    0.0       0.0   
2022-03-19 00:00:00+00:00       0.0      0.0      0.0    0.0    0.0       0.0   
2022-03-20 00:00:00+00:00       0.0      0.0      0.0    0.0    0.0       0.0   
2022-03-21 00:00:00+00:00       0.0      0.0      0.0    0.0    0.0       0.0   
2022-03-22 00:00:00+00:00       0.0      0.0      0.0    0.0    0.0       0.0   
2022-03-23 00:00:00+00:00       0.0      0.0      0.0    0.0    0.0       0.0   
2022-03-24 00:00:00+00:00       0.0      0.0      0.0    0.0    0.0       0.0   
2022-03-25 00:00:00+00:00       0.0      0.0      0.0    0.0    0.0       0.0   
2022-03-26 00:00:00+00:00       0.0      0.0      0.0    0.0    0.0       0.0   
2022-03-27 00:00:00+00:00       0.0      0.0      0.0    0.0    0.0       0.0   
2022-03-28 00:00:00+00:00       0.0      0.0      0.0    0.0    0.0       0.0   
2022-03-29 00:00:00+00:00       0.0      0.0      0.0    0.0    0.0       0.0   
2022-03-30 00:00:00+00:00       0.0      0.0      0.0    0.0    0.0       0.0   
2022-03-31 00:00:00+00:00       0.0      0.0      0.0    0.0    0.0       0.0   
2022-04-01 00:00:00+00:00       0.0      0.0      0.0    0.0    0.0       0.0   
2022-04-02 00:00:00+00:00       0.0      0.0      0.0    0.0    0.0       0.0   
2022-04-03 00:00:00+00:00       0.0      0.0      0.0    0.0    0.0       0.0   
2022-04-04 00:00:00+00:00       0.0      0.0      0.0    0.0    0.0       0.0   
2022-04-05 00:00:00+00:00       0.0      0.0      0.0    0.0    0.0       0.0   
2022-04-06 00:00:00+00:00       0.0      0.0      0.0    0.0    0.0       0.0   
2022-04-07 00:00:00+00:00       0.0      0.0      0.0    0.0    0.0       0.0   
2022-04-08 00:00:00+00:00       0.0      0.0      0.0    0.0    0.0       0.0   
2022-04-09 00:00:00+00:00       0.0      0.0      0.0    0.0    0.0       0.0   
2022-04-10 00:00:00+00:00       0.0      0.0      0.0    0.0    0.0       0.0   
2022-04-11 00:00:00+00:00       0.0      0.0      0.0    0.0    0.0       0.0   
2022-04-12 00:00:00+00:00       0.0      0.0      0.0    0.0    0.0       0.0   
2022-04-13 00:00:00+00:00       0.0      0.0      0.0    0.0    0.0       0.0   
2022-04-14 00:00:00+00:00       0.0      0.0      0.0    0.0    0.0       0.0   
2022-04-15 00:00:00+00:00       0.0  56506.0  58972.0    0.0    0.0       0.0   
2022-04-16 00:00:00+00:00       0.0   1561.0   1835.0    0.0    0.0       0.0   
2022-04-17 00:00:00+00:00       0.0   1344.0   1741.0    0.0    0.0       0.0   
2022-04-18 00:00:00+00:00       0.0   1513.0   2006.0    0.0    0.0       0.0   
2022-04-19 00:00:00+00:00       0.0    340.0    404.0    0.0    0.0       0.0   
2022-04-20 00:00:00+00:00       0.0   2640.0   3597.0    0.0    0.0       0.0   
2022-04-21 00:00:00+00:00       0.0   1496.0   2065.0    0.0    0.0       0.0   
2022-04-22 00:00:00+00:00       0.0   1668.0   2109.0    0.0    0.0       0.0   
2022-04-23 00:00:00+00:00       0.0   1516.0   2019.0    0.0    0.0       0.0   
2022-04-24 00:00:00+00:00       0.0   1618.0   2128.0    0.0  

In [102]:
# Excel does not support datetimes with timezones. Please ensure that datetimes are timezone unaware before writing to Excel.
# need to deal with
combine_df.index = combine_df.index.tz_localize(None)

In [103]:
combine_df.to_excel("consumption.xlsx",
             sheet_name='daily consump by meter')  

#### due to the poor quality of the data, need to conduct data cleansing process to make the data available to forecast
* replace 0 as nan
* use interpolation method to fill na

In [104]:
process_df = combine_df.copy()

In [105]:
process_df.describe()

T100         T2148         T2088  T2100  T2076           T184  \
count     182.000000    182.000000    182.000000  182.0  182.0     182.000000   
mean     8349.576923   1618.884615   1928.912088    0.0    0.0    9417.505495   
std     43190.116475   5876.957154   6902.592725    0.0    0.0   56451.826613   
min         0.000000      0.000000      0.000000    0.0    0.0       0.000000   
25%         0.000000      0.000000      0.000000    0.0    0.0       0.000000   
50%         0.000000      0.000000      0.000000    0.0    0.0       0.000000   
75%      2597.500000   1535.500000   1934.750000    0.0    0.0    1349.500000   
max    459744.000000  56506.000000  58972.000000    0.0    0.0  698616.000000   

               T112           T172           T148  
count  1.820000e+02     182.000000     182.000000  
mean   1.590714e+04   16200.329670   11175.324176  
std    1.001011e+05   84093.839365   51215.888482  
min    0.000000e+00       0.000000       0.000000  
25%    0.000000e+00       0.000000       0.000000  
50%    0.000000e+00       0.000000       0.000000  
75%    5.755000e+03    6355.500000    3786.250000  
max    1.259886e+06  937136.000000  446841.000000

In [106]:
process_df = process_df.replace(0, np.nan)

In [107]:
process_df

T100    T2148    T2088  T2100  T2076      T184  \
iotDataList_dataTime                                                       
2022-03-08                 NaN    466.0    528.0    NaN    NaN       NaN   
2022-03-09                 NaN   1352.0   1483.0    NaN    NaN       NaN   
2022-03-10                 NaN   1424.0   1518.0    NaN    NaN       NaN   
2022-03-11                 NaN   1062.0   1191.0    NaN    NaN       NaN   
2022-03-12                 NaN      NaN      NaN    NaN    NaN       NaN   
2022-03-13                 NaN      NaN      NaN    NaN    NaN       NaN   
2022-03-14                 NaN      NaN      NaN    NaN    NaN       NaN   
2022-03-15                 NaN      NaN      NaN    NaN    NaN       NaN   
2022-03-16                 NaN      NaN      NaN    NaN    NaN       NaN   
2022-03-17                 NaN      NaN      NaN    NaN    NaN       NaN   
2022-03-18                 NaN      NaN      NaN    NaN    NaN       NaN   
2022-03-19                 NaN      NaN      NaN    NaN    NaN       NaN   
2022-03-20                 NaN      NaN      NaN    NaN    NaN       NaN   
2022-03-21                 NaN      NaN      NaN    NaN    NaN       NaN   
2022-03-22                 NaN      NaN      NaN    NaN    NaN       NaN   
2022-03-23                 NaN      NaN      NaN    NaN    NaN       NaN   
2022-03-24                 NaN      NaN      NaN    NaN    NaN       NaN   
2022-03-25                 NaN      NaN      NaN    NaN    NaN       NaN   
2022-03-26                 NaN      NaN      NaN    NaN    NaN       NaN   
2022-03-27                 NaN      NaN      NaN    NaN    NaN       NaN   
2022-03-28                 NaN      NaN      NaN    NaN    NaN       NaN   
2022-03-29                 NaN      NaN      NaN    NaN    NaN       NaN   
2022-03-30                 NaN      NaN      NaN    NaN    NaN       NaN   
2022-03-31                 NaN      NaN      NaN    NaN    NaN       NaN   
2022-04-01                 NaN      NaN      NaN    NaN    NaN       NaN   
2022-04-02                 NaN      NaN      NaN    NaN    NaN       NaN   
2022-04-03                 NaN      NaN      NaN    NaN    NaN       NaN   
2022-04-04                 NaN      NaN      NaN    NaN    NaN       NaN   
2022-04-05                 NaN      NaN      NaN    NaN    NaN       NaN   
2022-04-06                 NaN      NaN      NaN    NaN    NaN       NaN   
2022-04-07                 NaN      NaN      NaN    NaN    NaN       NaN   
2022-04-08                 NaN      NaN      NaN    NaN    NaN       NaN   
2022-04-09                 NaN      NaN      NaN    NaN    NaN       NaN   
2022-04-10                 NaN      NaN      NaN    NaN    NaN       NaN   
2022-04-11                 NaN      NaN      NaN    NaN    NaN       NaN   
2022-04-12                 NaN      NaN      NaN    NaN    NaN       NaN   
2022-04-13                 NaN      NaN      NaN    NaN    NaN       NaN   
2022-04-14                 NaN      NaN      NaN    NaN    NaN       NaN   
2022-04-15                 NaN  56506.0  58972.0    NaN    NaN       NaN   
2022-04-16                 NaN   1561.0   1835.0    NaN    NaN       NaN   
2022-04-17                 NaN   1344.0   1741.0    NaN    NaN       NaN   
2022-04-18                 NaN   1513.0   2006.0    NaN    NaN       NaN   
2022-04-19                 NaN    340.0    404.0    NaN    NaN       NaN   
2022-04-20                 NaN   2640.0   3597.0    NaN    NaN       NaN   
2022-04-21                 NaN   1496.0   2065.0    NaN    NaN       NaN   
2022-04-22                 NaN   1668.0   2109.0    NaN    NaN       NaN   
2022-04-23                 NaN   1516.0   2019.0    NaN    NaN       NaN   
2022-04-24                 NaN   1618.0   2128.0    NaN    NaN       NaN   
2022-04-25                 NaN   1649.0   2105.0    NaN    NaN       NaN   
2022-04-26                 NaN   1465.0   2113.0    NaN    NaN       NaN   
2022-04-27                 NaN   1349.0   1936.0    NaN    NaN       NaN  

In [109]:
list(process_df['T100'])


[nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 459744.0,
 6380.0,
 529.0,
 nan,
 nan,
 nan,
 33923.0,
 7274.0,
 9803.0,
 9130.0,
 9018.0,
 9969.0,
 12288.0,
 8410.0,
 7193.0,
 15871.0,
 12735.0,
 2188.0,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 113903.0,
 10682.0,
 10324.0,
 13378.0,
 16158.0,
 18142.0,
 13290.0,
 8788.0,
 3864.0,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 313936.0,
 8718.0,
 11146.0,
 9016.0,
 2734.0,
 10038.0,
 5661.0,
 8114.0,
 9598.0,
 9140.0,
 7529.0,
 8203.0,

In [119]:
k,t = 0, 0
l = []
for i in process_df['T100']:
    # t += i
    if np.isnan(i):
        k += 1
        t += 0
    else:
        t += i

    l.append(t)
print(k)
print(t)
print(l)

134
1519623.0
[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 459744.0, 466124.0, 466653.0, 466653.0, 466653.0, 466653.0, 500576.0, 507850.0, 517653.0, 526783.0, 535801.0, 545770.0, 558058.0, 566468.0, 573661.0, 589532.0, 602267.0, 604455.0, 604455.0, 604455.0, 604455.0, 604455.0, 604455.0, 604455.0, 604455.0, 604455.0, 604455.0, 604455.0, 604455.0, 604455.0, 604455.0, 718358.0, 729040.0, 739364.0, 752742.0, 768900.0, 787042.0, 800332.0, 809120.0, 812984.0, 812984.0, 812984.0, 812984.0, 812984.0, 812984.0, 812984.0, 812984.0, 812984.0, 812984.0, 812984.0, 812984.0, 812984.0, 812984.0, 812984.0, 812984.0, 812984.0, 812984.0, 812984.0, 812984.0, 812984.0, 812984.0, 812984.0, 812984.0, 812984.0, 1126920.0, 1135638.0, 1146784.0, 1155800.0, 1158534.0, 1168572.0, 1174233.0, 1182347.0, 1191945.0, 1201085.0, 1208614.0, 1216817.0, 123

* an easy way to solve it without a model


In [157]:
process_df1 = process_df.copy()

In [122]:
print(process_df['T100'].mean())
print(process_df['T100'].quantile(0.9))
print(process_df['T100'].quantile(0.95))

31658.8125
48716.00000000021
119777.04999999999


In [154]:
def smartFill(k:list):
    l = []
    for i in k:
        if np.isnan(i):
            l.append(k.mean())
        elif i > k.quantile(0.95):
            l.append(k.mean())
        else:
            l.append(i)
    return l


           


In [149]:
pd.Series(smartFill(process_df1['T100']))

[31658.8125, 31658.8125, 31658.8125, 31658.8125, 31658.8125, 31658.8125, 31658.8125, 31658.8125, 31658.8125, 31658.8125, 31658.8125, 31658.8125, 31658.8125, 31658.8125, 31658.8125, 31658.8125, 31658.8125, 31658.8125, 31658.8125, 31658.8125, 31658.8125, 31658.8125, 31658.8125, 31658.8125, 31658.8125, 31658.8125, 31658.8125, 31658.8125, 31658.8125, 31658.8125, 31658.8125, 31658.8125, 31658.8125, 31658.8125, 31658.8125, 31658.8125, 31658.8125, 31658.8125, 31658.8125, 31658.8125, 31658.8125, 31658.8125, 31658.8125, 31658.8125, 31658.8125, 31658.8125, 31658.8125, 31658.8125, 31658.8125, 31658.8125, 31658.8125, 31658.8125, 31658.8125, 31658.8125, 31658.8125, 31658.8125, 31658.8125, 31658.8125, 31658.8125, 31658.8125, 31658.8125, 31658.8125, 31658.8125, 31658.8125, 31658.8125, 31658.8125, 31658.8125, 31658.8125, 31658.8125, 31658.8125, 31658.8125, 6380.0, 529.0, 31658.8125, 31658.8125, 31658.8125, 33923.0, 7274.0, 9803.0, 9130.0, 9018.0, 9969.0, 12288.0, 8410.0, 7193.0, 15871.0, 12735.0, 2188

/var/folders/xj/93j1__ws08j4839__kqrvwtc0000gp/T/ipykernel_65996/2027932303.py:1: FutureWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify a dtype explicitly to silence this warning.
  pd.Series(smartFill(process_df1['T100']))


Series([], dtype: float64)

In [155]:
process_df1['T100'] = pd.Series(smartFill(process_df1['T100']))

In [159]:
process_df2 = pd.DataFrame(index=process_df1.index)
for i in process_df1.columns:
    process_df2[i] = smartFill(process_df1[i])

In [165]:
process_df2

T100        T2148        T2088  T2100  T2076  \
iotDataList_dataTime                                                        
2022-03-08             31658.8125   466.000000   528.000000    0.0    0.0   
2022-03-09             31658.8125  1352.000000  1483.000000    0.0    0.0   
2022-03-10             31658.8125  1424.000000  1518.000000    0.0    0.0   
2022-03-11             31658.8125  1062.000000  1191.000000    0.0    0.0   
2022-03-12             31658.8125  3466.317647  4130.141176    0.0    0.0   
2022-03-13             31658.8125  3466.317647  4130.141176    0.0    0.0   
2022-03-14             31658.8125  3466.317647  4130.141176    0.0    0.0   
2022-03-15             31658.8125  3466.317647  4130.141176    0.0    0.0   
2022-03-16             31658.8125  3466.317647  4130.141176    0.0    0.0   
2022-03-17             31658.8125  3466.317647  4130.141176    0.0    0.0   
2022-03-18             31658.8125  3466.317647  4130.141176    0.0    0.0   
2022-03-19             31658.8125  3466.317647  4130.141176    0.0    0.0   
2022-03-20             31658.8125  3466.317647  4130.141176    0.0    0.0   
2022-03-21             31658.8125  3466.317647  4130.141176    0.0    0.0   
2022-03-22             31658.8125  3466.317647  4130.141176    0.0    0.0   
2022-03-23             31658.8125  3466.317647  4130.141176    0.0    0.0   
2022-03-24             31658.8125  3466.317647  4130.141176    0.0    0.0   
2022-03-25             31658.8125  3466.317647  4130.141176    0.0    0.0   
2022-03-26             31658.8125  3466.317647  4130.141176    0.0    0.0   
2022-03-27             31658.8125  3466.317647  4130.141176    0.0    0.0   
2022-03-28             31658.8125  3466.317647  4130.141176    0.0    0.0   
2022-03-29             31658.8125  3466.317647  4130.141176    0.0    0.0   
2022-03-30             31658.8125  3466.317647  4130.141176    0.0    0.0   
2022-03-31             31658.8125  3466.317647  4130.141176    0.0    0.0   
2022-04-01             31658.8125  3466.317647  4130.141176    0.0    0.0   
2022-04-02             31658.8125  3466.317647  4130.141176    0.0    0.0   
2022-04-03             31658.8125  3466.317647  4130.141176    0.0    0.0   
2022-04-04             31658.8125  3466.317647  4130.141176    0.0    0.0   
2022-04-05             31658.8125  3466.317647  4130.141176    0.0    0.0   
2022-04-06             31658.8125  3466.317647  4130.141176    0.0    0.0   
2022-04-07             31658.8125  3466.317647  4130.141176    0.0    0.0   
2022-04-08             31658.8125  3466.317647  4130.141176    0.0    0.0   
2022-04-09             31658.8125  3466.317647  4130.141176    0.0    0.0   
2022-04-10             31658.8125  3466.317647  4130.141176    0.0    0.0   
2022-04-11             31658.8125  3466.317647  4130.141176    0.0    0.0   
2022-04-12             31658.8125  3466.317647  4130.141176    0.0    0.0   
2022-04-13             31658.8125  3466.317647  4130.141176    0.0    0.0   
2022-04-14             31658.8125  3466.317647  4130.141176    0.0    0.0   
2022-04-15             31658.8125  3466.317647  4130.141176    0.0    0.0   
2022-04-16             31658.8125  1561.000000  1835.000000    0.0    0.0   
2022-04-17             31658.8125  1344.000000  1741.000000    0.0    0.0   
2022-04-18             31658.8125  1513.000000  2006.000000    0.0    0.0   
2022-04-19             31658.8125   340.000000   404.000000    0.0    0.0   
2022-04-20             31658.8125  2640.000000  3597.000000    0.0    0.0   
2022-04-21             31658.8125  1496.000000  2065.000000    0.0    0.0   
2022-04-22             31658.8125  1668.000000  2109.000000    0.0    0.0   
2022-04-23             31658.8125  1516.000000  2019.000000    0.0    0.0   
2022-04-24             31658.8125  1618.000000  2128.000000    0.0    0.0   
2022-04-25             31658.8125  1649.000000  2105.000000    0.0    0.0   
2022-04-26             31658.8125  1465.000000  2113.000000    0.0    0.0   
2022-04-27             31

In [164]:
process_df2 = process_df2.fillna(0)


#### Use ARIMA to forecast next 7 days value


In [167]:
process_df2.tail(5)


T100        T2148        T2088  T2100  T2076  \
iotDataList_dataTime                                                       
2022-09-01            31658.8125  3466.317647  4130.141176    0.0    0.0   
2022-09-02            83233.0000  6968.000000  4130.141176    0.0    0.0   
2022-09-03             6530.0000  1497.000000  1789.000000    0.0    0.0   
2022-09-04            31658.8125  3466.317647  4130.141176    0.0    0.0   
2022-09-05            14023.0000  3033.000000  4016.000000    0.0    0.0   

                              T184           T112      T172           T148  
iotDataList_dataTime                                                        
2022-09-01            35708.041667   60314.583333  61426.25   42373.104167  
2022-09-02            35708.041667  196914.000000  61426.25  226914.000000  
2022-09-03             9628.000000   13482.000000  16344.00   10449.000000  
2022-09-04            35708.041667   60314.583333  61426.25   42373.104167  
2022-09-05            18836.000000   27138.000000  34792.00   22832.000000

In [171]:
ARIMA(process_df2['T100'], order= (2,3,7)).fit().forecast(steps=7, frequency='D')


/Library/Frameworks/Python.framework/Versions/3.10/lib/python3.10/site-packages/statsmodels/tsa/base/tsa_model.py:471: ValueWarning: No frequency information was provided, so inferred frequency D will be used.
  self._init_dates(dates, freq)
/Library/Frameworks/Python.framework/Versions/3.10/lib/python3.10/site-packages/statsmodels/tsa/base/tsa_model.py:471: ValueWarning: No frequency information was provided, so inferred frequency D will be used.
  self._init_dates(dates, freq)
/Library/Frameworks/Python.framework/Versions/3.10/lib/python3.10/site-packages/statsmodels/tsa/base/tsa_model.py:471: ValueWarning: No frequency information was provided, so inferred frequency D will be used.
  self._init_dates(dates, freq)
/Library/Frameworks/Python.framework/Versions/3.10/lib/python3.10/site-packages/statsmodels/tsa/statespace/sarimax.py:978: UserWarning: Non-invertible starting MA parameters found. Using zeros as starting parameters.
  warn('Non-invertible starting MA parameters found.'
/Li

2022-09-06    28109.980886
2022-09-07    27046.995903
2022-09-08    28093.425196
2022-09-09    29263.260700
2022-09-10    27569.448244
2022-09-11    30783.238099
2022-09-12    27447.063208
Freq: D, Name: predicted_mean, dtype: float64

In [172]:
# prediction file

pred = {}

for i in process_df2.columns:
    pred[i] = ARIMA(process_df2[i], order= (2,3,7)).fit().forecast(steps=7)


/Library/Frameworks/Python.framework/Versions/3.10/lib/python3.10/site-packages/statsmodels/tsa/base/tsa_model.py:471: ValueWarning: No frequency information was provided, so inferred frequency D will be used.
  self._init_dates(dates, freq)
/Library/Frameworks/Python.framework/Versions/3.10/lib/python3.10/site-packages/statsmodels/tsa/base/tsa_model.py:471: ValueWarning: No frequency information was provided, so inferred frequency D will be used.
  self._init_dates(dates, freq)
/Library/Frameworks/Python.framework/Versions/3.10/lib/python3.10/site-packages/statsmodels/tsa/base/tsa_model.py:471: ValueWarning: No frequency information was provided, so inferred frequency D will be used.
  self._init_dates(dates, freq)
/Library/Frameworks/Python.framework/Versions/3.10/lib/python3.10/site-packages/statsmodels/tsa/statespace/sarimax.py:978: UserWarning: Non-invertible starting MA parameters found. Using zeros as starting parameters.
  warn('Non-invertible starting MA parameters found.'
/Li

In [174]:
pred1 = pd.DataFrame(pred)

In [175]:
pred1


T100        T2148        T2088  T2100  T2076  \
2022-09-06  28109.980886  2511.018945  3666.371942    0.0    0.0   
2022-09-07  27046.995903  3510.251798  4114.442627    0.0    0.0   
2022-09-08  28093.425196  2759.336357  3701.518775    0.0    0.0   
2022-09-09  29263.260700  3188.677180  3962.259802    0.0    0.0   
2022-09-10  27569.448244  3163.359636  3973.039956    0.0    0.0   
2022-09-11  30783.238099  2821.454757  3798.090141    0.0    0.0   
2022-09-12  27447.063208  3434.475245  4191.007976    0.0    0.0   

                    T184          T112          T172          T148  
2022-09-06  25924.226912  16269.668650  51028.558013  57018.457721  
2022-09-07  26624.867239  56389.335140  46968.452745  53949.661480  
2022-09-08  26554.477694  35866.571642  50181.732996  60960.342968  
2022-09-09  27323.499119  44661.241531  49992.811781  57829.619389  
2022-09-10  27144.312765  51783.392138  48743.956995  61967.913630  
2022-09-11  27695.511811  29965.753476  52377.823098  61330.888759  
2022-09-12  27760.616792  56478.970318  48107.680397  62391.684412

In [176]:
process_df2.tail(5)

T100        T2148        T2088  T2100  T2076  \
iotDataList_dataTime                                                       
2022-09-01            31658.8125  3466.317647  4130.141176    0.0    0.0   
2022-09-02            83233.0000  6968.000000  4130.141176    0.0    0.0   
2022-09-03             6530.0000  1497.000000  1789.000000    0.0    0.0   
2022-09-04            31658.8125  3466.317647  4130.141176    0.0    0.0   
2022-09-05            14023.0000  3033.000000  4016.000000    0.0    0.0   

                              T184           T112      T172           T148  
iotDataList_dataTime                                                        
2022-09-01            35708.041667   60314.583333  61426.25   42373.104167  
2022-09-02            35708.041667  196914.000000  61426.25  226914.000000  
2022-09-03             9628.000000   13482.000000  16344.00   10449.000000  
2022-09-04            35708.041667   60314.583333  61426.25   42373.104167  
2022-09-05            18836.000000   27138.000000  34792.00   22832.000000

In [177]:
with pd.ExcelWriter('process_and_prediction.xlsx') as writer:  
    process_df2.to_excel(writer, sheet_name='processed data')
    pred1.to_excel(writer, sheet_name='prediction')

In [179]:
# for commit, test 